### Inference of DBT lesion detection 

Input 
- csv with the path to the images

Output
- csv with lesion bounding boxes


In [1]:
import os
os.environ['CUDA_DEVICE_ORDER']='PCI_BUS_ID'
os.environ['CUDA_VISIBLE_DEVICES']='1'



In [3]:
# install dependencies: 
# !pip install pyyaml==5.1
import torch, torchvision
import tensorflow
print(torch.__version__, torch.cuda.is_available())
!gcc --version


1.7.0 True
gcc (Ubuntu 5.4.0-6ubuntu1~16.04.11) 5.4.0 20160609
Copyright (C) 2015 Free Software Foundation, Inc.
This is free software; see the source for copying conditions.  There is NO
warranty; not even for MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.



In [3]:
import torch
assert torch.__version__.startswith("1.7")


In [4]:
# Some basic setup:
import detectron2
from detectron2.utils.logger import setup_logger
setup_logger()

# import some common libraries
%matplotlib inline
from matplotlib import pyplot as plt
import numpy as np
import os, json, cv2, random

# import some common detectron2 utilities
from detectron2 import model_zoo
from detectron2.engine import DefaultPredictor
from detectron2.config import get_cfg
from detectron2.utils.visualizer import Visualizer
from detectron2.data import MetadataCatalog, DatasetCatalog



** fvcore version of PathManager will be deprecated soon. **
** Please migrate to the version in iopath repo. **
https://github.com/facebookresearch/iopath 



In [5]:
# parameters for N
start_pred = 2 # start_pred:end to look for prediction not implemented
end_pred = 2 # end_pred to look for prediction not implemented (all slices are used)
min_score = 0.01 # minimum score to keep prediction
min_iou = 0.5 #0.75 # minimum iou to look for overlappin boxes.

output_csv = 'test_results_omidb_R2_101_2slices_sc'+str(min_score)+'_iou'+ str(min_iou)+'.csv'

model_file = "model_final_R2_101_omidb_10k_dbt.pth"
config_file = "config_trained_R2_101_10k.yaml"


In [6]:
# load trained network 

cfg = get_cfg()
cfg.merge_from_file("./output/"+config_file)
#Use the final weights generated after successful training for inference  
cfg.MODEL.WEIGHTS = os.path.join(cfg.OUTPUT_DIR, model_file)
cfg.MODEL.ROI_HEADS.SCORE_THRESH_TEST = min_score # set the testing threshold for this model
cfg.DATASETS.TEST = ("DBT_train", )
predictor = DefaultPredictor(cfg)
test_metadata = MetadataCatalog.get("DBT_train")


In [7]:
import os

%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd

from duke_dbt_data import dcmread_image, read_boxes, draw_box

# imports 
import omidb
import numpy as np
import cv2
import csv


In [8]:
#loading the images
base_path = "/mnt/mia_images/breast/DBT-Challenge/DBT_test"

# validation
# df = pd.read_csv(base_path+"/BCS-DBT file-paths-validation.csv")

df = pd.read_csv(base_path+"/BCS-DBT file-paths-test.csv")


In [9]:
print(df)

      PatientID    StudyUID  View  \
0    DBT-P00036  DBT-S03354   lcc   
1    DBT-P00036  DBT-S03354  lmlo   
2    DBT-P00036  DBT-S03354   rcc   
3    DBT-P00036  DBT-S03354  rmlo   
4    DBT-P00087  DBT-S04170   lcc   
..          ...         ...   ...   
596  DBT-P05036  DBT-S00311  lmlo   
597  DBT-P05049  DBT-S01458   lcc   
598  DBT-P05049  DBT-S01458  lmlo   
599  DBT-P05049  DBT-S01458   rcc   
600  DBT-P05049  DBT-S01458  rmlo   

                                      descriptive_path  \
0    Breast-Cancer-Screening-DBT/DBT-P00036/01-01-2...   
1    Breast-Cancer-Screening-DBT/DBT-P00036/01-01-2...   
2    Breast-Cancer-Screening-DBT/DBT-P00036/01-01-2...   
3    Breast-Cancer-Screening-DBT/DBT-P00036/01-01-2...   
4    Breast-Cancer-Screening-DBT/DBT-P00087/01-01-2...   
..                                                 ...   
596  Breast-Cancer-Screening-DBT/DBT-P05036/01-01-2...   
597  Breast-Cancer-Screening-DBT/DBT-P05049/01-01-2...   
598  Breast-Cancer-Screening-DBT/

In [10]:
output_path = '/home/robert/data/DBT'
# create folders
try:
    os.mkdir(output_path)     
except OSError as e:
    if (e.errno != 17): 
        print("copy_case: creation of %s failed" % output_path)
        print(e)


In [11]:
def get_normal_BBox (image):
    #threshold image 
    img = cv2.threshold(image, 0, 255, cv2.THRESH_BINARY)[1]  # ensure binary
#     plt.imshow(img,'gray')#,vmin=0,vmax=255))
#     plt.show()
    nb_components, output, stats, centroids = cv2.connectedComponentsWithStats(img, connectivity=4)
    sizes = stats[:, -1]
    max_label = 1
    max_size = sizes[1]
    for i in range(2, nb_components):
        if sizes[i] > max_size:
            max_label = i
            max_size = sizes[i]
    img2 = np.zeros(output.shape,dtype=np.uint8)
    img2[output == max_label] = 255
#     plt.imshow(img2,'gray')
#     plt.show()
#     input("Press Enter to continue...")
    contours, hierarchy = cv2.findContours(img2,cv2.RETR_TREE,cv2.CHAIN_APPROX_NONE)

    cnt = contours[0]
    aux_im = img2
    x,y,w,h = cv2.boundingRect(cnt)
#     cv2.rectangle(aux_im,(x,y),(x+w,y+h),(255,0,0),5)
#     plt.imshow(aux_im)
#     plt.show()
    #input("Press Enter to continue...")
    out_bbox = omidb.mark.BoundingBox(x, y, x+w, y+h)
    
    return out_bbox, img2 # returns bounding box and mask image. 

In [12]:
from detectron2.utils.visualizer import ColorMode
        
def predict_slice(view, client, episode,image_org,side):
    
#   Assuming windowWidth has been already applied (see Duke code)    
#     if 'WindowWidth' in image.dcm:
#         #print('Image hs windowing')
#         image_2d = apply_voi_lut(image.dcm.pixel_array, image.dcm)
#     else: image_2d = image.dcm.pixel_array
    # Rescaling grey scale between 0-255
    
    dims = image_org.shape
   
    image_2d_scaled = (np.maximum(image_org,0) / image_org.max()) * 255.0

    # Convert to uint
    image_2d_scaled = np.uint8(image_2d_scaled)
    
    # make a copy of the original image
    image_2d = np.copy(image_2d_scaled)
    
    if (side=='r' or side=='R'): # flip image and ROI coordinates.
        image_2d =cv2.flip(image_2d, 1)
      
    # obtain main breast area
    bbox,mask = get_normal_BBox(image_2d)
    
    #crop image to predict
    image_crop = image_2d[bbox.y1:bbox.y2,bbox.x1:bbox.x2]
    image_crop = np.reshape(image_crop,image_crop.shape+(1,))
    
    image_crop =  cv2.cvtColor(image_crop,cv2.COLOR_GRAY2RGB)
      
    outputs = predictor(image_crop)
    out = outputs["instances"].to("cpu")
    if (len(out.scores)>0):
#         print(out.pred_boxes)
#         print(out.scores)    
#         v = v.draw_instance_predictions(outputs["instances"].to("cpu")) #Passing the predictions to CPU from the GPU
#         plt.imshow(v.get_image()[:, :, ::-1])
#         plt.show()
    
        for score, pred_box in zip(out.scores, out.pred_boxes):
#             print(pred_box, score)
            # adapt bbox_ROI to original  image (add bbox.x1 and bbox.y1)
            pred_box[0] += bbox.x1
            pred_box[2] += bbox.x1
            pred_box[1] += bbox.y1
            pred_box[3] += bbox.y1
            if (side=='r' or side=='R'): 
                # flip bounding box back in case of R image         
                aux = float(pred_box[2])
                pred_box[2] = dims[1]-pred_box[0] 
                pred_box[0] = dims[1]-aux                 
#         print(out.pred_boxes)
#         print(out.scores)       
    
    return out.pred_boxes, out.scores
    
    

In [13]:
def NMS_volume (pred_boxes_vol,pred_scores_vol):
    # todo perform thresholding or NMS
    final_boxes_vol = []
    final_scores_vol = []
    final_slices_vol = []
      
    length = len(pred_boxes_vol)
    
    # checking slice i against all other slices (doing a cat)           
    all_boxes = detectron2.structures.Boxes.cat(pred_boxes_vol[:])
    all_scores =  torch.squeeze(torch.cat([b for b in pred_scores_vol[:]], dim=0))    
     
    for i in range(0,length):
        if (len(pred_boxes_vol[i])>0):   
            # there is more than one annotation.
            if (all_scores.dim()>0):
                # check if there is overlap
                iou_matrix = torch.squeeze(detectron2.structures.pairwise_iou(pred_boxes_vol[i], all_boxes))
                j = 0

                for box, score in zip(pred_boxes_vol[i],pred_scores_vol[i]):
                    if (iou_matrix.dim()>1):
                        idx_s = ((iou_matrix[j,:] > min_iou).nonzero())
                    else: idx_s = ((iou_matrix > min_iou).nonzero())
                    # condition 1: my score is larger or equal than all other overlapping boxes (idx_s)
                    if (score >= torch.max(all_scores[idx_s])):
                        if (score >= min_score):
#                             print("adding slice ",i+start_pred, score, box)
                            final_boxes_vol.append(box)
                            final_scores_vol.append(score)
                            final_slices_vol.append(i+start_pred)
                    j +=1
            else: # there is only one annotatio only check threshold.
                for box, score in zip(pred_boxes_vol[i],pred_scores_vol[i]):
                    if (score >= min_score):
#                         print("adding slice ",i+start_pred, score, box)
                        final_boxes_vol.append(box)
                        final_scores_vol.append(score)
                        final_slices_vol.append(i+start_pred)
#     print('Final Boxes')
#     print(final_boxes_vol)
#     print(final_scores_vol)
#     print(final_slices_vol)    
    return final_boxes_vol ,final_scores_vol, final_slices_vol

    
    
   

In [14]:
 

def write_csv (final_boxes_vol, final_scores_vol, final_slices_vol, client, episode, view, total_slices):
      
# write CSV with coordinates 
#     depth = int(total_slices/8) Changed to 0. 
# depth for the evaluation of the challenge is not important, only used to get the central slice (and we have that)
    depth = 0
    with open(output_path+'/'+output_csv, 'a+', newline='') as file:
        writer = csv.writer(file)
        for box, score,slice_num in zip(final_boxes_vol,final_scores_vol, final_slices_vol):
            
            print(client, episode, view, int(box[0]),int(box[2]-box[0]), int(box[1]), int(box[3]-box[1]),
                  max(0,slice_num-depth),  min(total_slices-1, slice_num+depth)-max(0,slice_num-depth),float(score))
            writer.writerow([client, episode, view, int(box[0]),int(box[2]-box[0]), int(box[1]), int(box[3]-box[1]),
                  max(0,slice_num-depth),  min(total_slices-1, slice_num+depth)-max(0,slice_num-depth),float(score)])
        
# PatientID: string - patient identifier
# StudyUID: string - study identifier
# View: string - view name, one of: RLL, LCC, RMLO, LMLO
# X: integer - X coordinate (on the horizontal axis) of the left edge of the predicted bounding box in 0-based indexing (for the left-most column of the image x=0)
# Width: integer - predicted bounding box width (along the horizontal axis)
# Y: integer - Y coordinate (on the vertical axis) of the top edge of the predicted bounding box in 0-based indexing (for the top-most column of the image y=0)
# Height: integer - predicted bounding box height (along the vertical axis)
# Z: integer - the first bounding box slice number in 0-based indexing (for the first slice of the image z=0)
# Depth: integer - predicted bounding box slice span (size along the depth axis)
# Score: float - predicted bounding box confidence score indicating the confidence level that the detection represents an actual lesion. This score can have an arbitrary scale, but has to be unified across all the cases within a single submission (e.g. 0.0 – 1.0)
# Example:
# PatientID,StudyUID,View,X,Width,Y,Height,Z,Depth,Score ID1,UID1,RLL,X(int),Width(int),Y(int),Height(int),Z(int),Depth(int),Score(float) ID2,UID2,LCC,X(int),Width(int),Y(int),Height(int),Z(int),Depth(int),Score(float) ID3,UID3,RMLO,X(int),Width(int),Y(int),Height(int),Z(int),Depth(int),Score(float) ID4,UID4,LMLO,X(int),Width(int),Y(int),Height(int),Z(int),Depth(int),Score(float)                      

In [15]:
plt.rcParams['figure.figsize'] = [12, 8]
plt.rcParams['figure.dpi'] = 100


with open(output_path+'/'+output_csv, 'w+', newline='') as file:
    writer = csv.writer(file)
    writer.writerow(['PatientID','StudyUID','View','X','Width','Y','Height','Z','Depth','Score'])


for index,view_series in df.iterrows():
    print(view_series)
    view = view_series["View"]
    # if you have image data saved in classic path folder structure, read the file path from "classic_path"
    # image_path = os.path.join("/data", view_series["classic_path"])
    image_path = os.path.join(base_path, view_series["descriptive_path"])
    print(image_path)
    
    
    client = view_series["PatientID"]
    episode = view_series["StudyUID"]

    side = view[0]
    pred_boxes_vol = []
    pred_scores_vol =[]
    image = dcmread_image(fp=image_path, view=view)   
    dims = image.shape
    for slice_index in range(dims[0]):

        if (slice_index >= start_pred and slice_index < dims[0]-end_pred ) :
            image_2d = image[slice_index,:,:]
            pred_boxes, pred_scores = predict_slice(view,client, episode,image_2d,side)
            pred_boxes_vol.insert(slice_index, pred_boxes)
            pred_scores_vol.insert(slice_index,pred_scores)
#         for box in pred_boxes:
#             print (box)
#             cv2.rectangle(image_2d,(int(box[0]),int(box[1])),(int(box[2]), int(box[3])),(255,255,255),5)
#             plt.imshow(image_2d)    
#         plt.show()         

    final_boxes_vol, final_scores_vol, final_slices_vol = NMS_volume (pred_boxes_vol,pred_scores_vol)
    write_csv (final_boxes_vol, final_scores_vol, final_slices_vol, client, episode, view, dims[0])
    #input("Press Enter to continue...")


PatientID                                                  DBT-P00036
StudyUID                                                   DBT-S03354
View                                                              lcc
descriptive_path    Breast-Cancer-Screening-DBT/DBT-P00036/01-01-2...
classic_path        Breast-Cancer-Screening-DBT/DBT-P00036/1.2.826...
Name: 0, dtype: object
/mnt/mia_images/breast/DBT-Challenge/DBT_test/Breast-Cancer-Screening-DBT/DBT-P00036/01-01-2000-DBT-S03354-MAMMO screening digital bilateral-14628/12278.000000-02208/1-1.dcm


/home/robert/miniconda2/envs/fast2/lib/python3.8/site-packages/openjpeg/utils.py:189: UserWarning: The (0028,0101) Bits Stored value '10' in the dataset does not match the component precision value '16' found in the JPEG 2000 data. It's recommended that you change the Bits Stored value to produce the correct output
  warnings.warn(
/home/robert/src/detectron2/Res2Net-detectron2/detectron2/modeling/roi_heads/fast_rcnn.py:110: UserWarning: This overload of nonzero is deprecated:
	nonzero()
Consider using one of the following signatures instead:
	nonzero(*, bool as_tuple) (Triggered internally at  /pytorch/torch/csrc/utils/python_arg_parser.cpp:882.)
  filter_inds = filter_mask.nonzero()


DBT-P00036 DBT-S03354 lcc 770 72 905 75 5 0 0.00020406495605129749
DBT-P00036 DBT-S03354 lcc 784 37 916 43 5 0 0.00013843255874235183
DBT-P00036 DBT-S03354 lcc 430 84 1107 81 9 0 0.0003343381395097822
DBT-P00036 DBT-S03354 lcc 420 143 1090 105 9 0 0.00011680846364470199
DBT-P00036 DBT-S03354 lcc 703 119 823 242 10 0 0.00012270454317331314
DBT-P00036 DBT-S03354 lcc 718 161 827 158 11 0 0.7293378710746765
DBT-P00036 DBT-S03354 lcc 672 215 784 258 11 0 0.006348859518766403
DBT-P00036 DBT-S03354 lcc 570 385 822 203 11 0 0.00015914406685624272
DBT-P00036 DBT-S03354 lcc 345 77 679 91 13 0 0.0002393566392129287
DBT-P00036 DBT-S03354 lcc 314 137 666 95 13 0 0.00014391254808288068
DBT-P00036 DBT-S03354 lcc 352 47 704 47 13 0 0.0001343955227639526
DBT-P00036 DBT-S03354 lcc 371 44 699 48 13 0 0.00012861737923230976
DBT-P00036 DBT-S03354 lcc 277 69 639 84 15 0 0.0001264797756448388
DBT-P00036 DBT-S03354 lcc 1153 45 1505 50 18 0 0.00014939927496016026
DBT-P00036 DBT-S03354 lcc 1141 65 1470 77 18 0 

DBT-P00036 DBT-S03354 rcc 1089 87 1642 98 2 0 0.00016846727521624416
DBT-P00036 DBT-S03354 rcc 1019 74 1412 91 3 0 0.0014172918163239956
DBT-P00036 DBT-S03354 rcc 1044 38 1411 100 3 0 0.0006358923274092376
DBT-P00036 DBT-S03354 rcc 1032 52 1435 58 3 0 0.0005550620844587684
DBT-P00036 DBT-S03354 rcc 1000 109 1396 137 3 0 0.0005055126966908574
DBT-P00036 DBT-S03354 rcc 1018 36 1407 104 3 0 0.0004858245374634862
DBT-P00036 DBT-S03354 rcc 1016 53 1438 59 3 0 0.0003282326797489077
DBT-P00036 DBT-S03354 rcc 1013 70 1451 70 3 0 0.00020121972193010151
DBT-P00036 DBT-S03354 rcc 1572 41 1359 46 3 0 0.00013115430192556232
DBT-P00036 DBT-S03354 rcc 1011 37 1445 68 3 0 0.00010712284711189568
DBT-P00036 DBT-S03354 rcc 808 141 1423 157 7 0 0.002796712564304471
DBT-P00036 DBT-S03354 rcc 1726 80 1627 56 8 0 0.11830286681652069
DBT-P00036 DBT-S03354 rcc 974 142 749 117 8 0 0.00026036586496047676
DBT-P00036 DBT-S03354 rcc 797 54 1248 40 8 0 0.00012994109420105815
DBT-P00036 DBT-S03354 rcc 1795 40 1611 72

DBT-P00087 DBT-S04170 lcc 238 78 1427 62 13 0 0.00010971449955832213
DBT-P00087 DBT-S04170 lcc 229 119 1399 120 14 0 0.0033306803088635206
DBT-P00087 DBT-S04170 lcc 262 57 1403 108 14 0 0.0004843033093493432
DBT-P00087 DBT-S04170 lcc 299 39 1444 89 18 0 0.00013861007755622268
DBT-P00087 DBT-S04170 lcc 314 37 1445 89 18 0 0.00013144576223567128
DBT-P00087 DBT-S04170 lcc 297 68 1460 56 18 0 0.00012627562682610005
DBT-P00087 DBT-S04170 lcc 1240 156 1220 126 19 0 0.00013637830852530897
DBT-P00087 DBT-S04170 lcc 250 139 1371 116 26 0 0.2563609480857849
DBT-P00087 DBT-S04170 lcc 312 58 1374 110 26 0 0.015746796503663063
DBT-P00087 DBT-S04170 lcc 225 212 1344 158 26 0 0.00543392775580287
DBT-P00087 DBT-S04170 lcc 181 597 671 1241 26 0 0.00020787713583558798
DBT-P00087 DBT-S04170 lcc 124 340 1265 389 26 0 0.00011486127914395183
DBT-P00087 DBT-S04170 lcc 579 82 1253 75 33 0 0.13344888389110565
DBT-P00087 DBT-S04170 lcc 581 75 1223 80 33 0 0.00010342153836973011
DBT-P00087 DBT-S04170 lcc 580 55 

...

DBT-P04975 DBT-S00578 rmlo 1407 87 985 103 3 0 0.00011678518785629421
DBT-P04975 DBT-S00578 rmlo 1387 84 966 101 4 0 0.0004843659116886556
DBT-P04975 DBT-S00578 rmlo 1385 75 935 190 4 0 0.00015587828238494694
DBT-P04975 DBT-S00578 rmlo 1529 81 1285 86 9 0 0.0003552180714905262
DBT-P04975 DBT-S00578 rmlo 1521 108 1249 140 9 0 0.00025112886214628816
DBT-P04975 DBT-S00578 rmlo 1546 46 1302 54 9 0 0.00013435556320473552
DBT-P04975 DBT-S00578 rmlo 1422 61 632 45 10 0 0.00013241633132565767
DBT-P04975 DBT-S00578 rmlo 1213 287 916 521 11 0 0.0038474821485579014
DBT-P04975 DBT-S00578 rmlo 1292 153 1229 182 11 0 0.0006911043892614543
DBT-P04975 DBT-S00578 rmlo 1284 107 1040 161 11 0 0.0002958177647087723
DBT-P04975 DBT-S00578 rmlo 1024 417 1744 326 17 0 0.03137822449207306
DBT-P04975 DBT-S00578 rmlo 1123 161 1765 280 17 0 0.00041615060763433576
DBT-P04975 DBT-S00578 rmlo 1064 130 1753 307 17 0 0.00011392297165002674
DBT-P04975 DBT-S00578 rmlo 949 576 1385 706 18 0 0.0005164125468581915
DBT-P049

DBT-P04982 DBT-S03578 rmlo 621 203 1024 161 2 0 0.017128797248005867
DBT-P04982 DBT-S03578 rmlo 665 74 1056 94 3 0 0.0002208738587796688
DBT-P04982 DBT-S03578 rmlo 1255 65 689 101 4 0 0.4236583709716797
DBT-P04982 DBT-S03578 rmlo 1404 74 457 57 4 0 0.00024978205328807235
DBT-P04982 DBT-S03578 rmlo 763 145 763 129 5 0 0.00010700289567466825
DBT-P04982 DBT-S03578 rmlo 1229 132 688 108 6 0 0.9914782643318176
DBT-P04982 DBT-S03578 rmlo 1057 53 860 51 7 0 0.0005418515065684915
DBT-P04982 DBT-S03578 rmlo 1048 83 849 79 7 0 0.0005139349377714097
DBT-P04982 DBT-S03578 rmlo 1039 81 849 48 7 0 0.00046719194506295025
DBT-P04982 DBT-S03578 rmlo 1076 50 863 49 7 0 0.0002814455365296453
DBT-P04982 DBT-S03578 rmlo 1100 48 871 46 7 0 0.0002355527540203184
DBT-P04982 DBT-S03578 rmlo 1033 50 848 52 7 0 0.00021600544278044254
DBT-P04982 DBT-S03578 rmlo 1080 68 848 48 7 0 0.0001309633516939357
DBT-P04982 DBT-S03578 rmlo 1775 84 942 52 8 0 0.002401897683739662
DBT-P04982 DBT-S03578 rmlo 1783 52 948 55 8 0 

DBT-P05036 DBT-S00311 lmlo 567 92 879 109 6 0 0.00016377080464735627
DBT-P05036 DBT-S00311 lmlo 425 49 1784 49 7 0 0.00011146712495246902
DBT-P05036 DBT-S00311 lmlo 589 97 705 99 8 0 0.00823850929737091
DBT-P05036 DBT-S00311 lmlo 611 62 716 72 8 0 0.0005494815413840115
DBT-P05036 DBT-S00311 lmlo 574 147 679 149 8 0 0.0003029988147318363
DBT-P05036 DBT-S00311 lmlo 986 78 986 77 9 0 0.0009990556864067912
DBT-P05036 DBT-S00311 lmlo 1001 53 999 54 9 0 0.0004053996526636183
DBT-P05036 DBT-S00311 lmlo 1018 32 985 75 9 0 0.0003245830594096333
DBT-P05036 DBT-S00311 lmlo 1016 51 1004 53 9 0 0.00018447595357429236
DBT-P05036 DBT-S00311 lmlo 959 138 994 80 9 0 0.00017140002455562353
DBT-P05036 DBT-S00311 lmlo 995 52 1015 50 9 0 0.00016554395551793277
DBT-P05036 DBT-S00311 lmlo 928 80 1644 75 9 0 0.00013210621546022594
DBT-P05036 DBT-S00311 lmlo 422 73 1752 68 9 0 0.00011096455273218453
DBT-P05036 DBT-S00311 lmlo 418 147 1753 118 10 0 0.023799583315849304
DBT-P05036 DBT-S00311 lmlo 457 50 1755 116

DBT-P05049 DBT-S01458 lmlo 133 66 1513 77 2 0 0.00011060568067478016
DBT-P05049 DBT-S01458 lmlo 626 52 1768 44 5 0 0.00014325972006190568
DBT-P05049 DBT-S01458 lmlo 850 64 1800 67 5 0 0.00014003155229147524
DBT-P05049 DBT-S01458 lmlo 847 46 1816 48 5 0 0.0001028387705446221
DBT-P05049 DBT-S01458 lmlo 912 71 1227 159 7 0 0.00011801166692748666
DBT-P05049 DBT-S01458 lmlo 860 141 1243 142 8 0 0.0007623327546752989
DBT-P05049 DBT-S01458 lmlo 879 89 1259 111 8 0 0.00019509586854837835
DBT-P05049 DBT-S01458 lmlo 222 50 1524 48 16 0 0.0694625973701477
DBT-P05049 DBT-S01458 lmlo 219 59 1542 36 16 0 0.019202830269932747
DBT-P05049 DBT-S01458 lmlo 201 73 1514 69 16 0 0.00795548502355814
DBT-P05049 DBT-S01458 lmlo 241 41 1521 54 16 0 0.004737387411296368
DBT-P05049 DBT-S01458 lmlo 218 38 1516 64 16 0 0.0047296215780079365
DBT-P05049 DBT-S01458 lmlo 213 50 1520 38 16 0 0.004625198431313038
DBT-P05049 DBT-S01458 lmlo 256 31 1524 41 16 0 0.0006458474672399461
DBT-P05049 DBT-S01458 lmlo 235 31 1505 7

DBT-P05049 DBT-S01458 rmlo 1566 32 95 69 2 0 0.0013831251999363303
DBT-P05049 DBT-S01458 rmlo 1561 23 95 75 2 0 0.00019821294699795544
DBT-P05049 DBT-S01458 rmlo 1569 49 100 51 4 0 0.00960264727473259
DBT-P05049 DBT-S01458 rmlo 1585 43 109 45 4 0 0.0022162252571433783
DBT-P05049 DBT-S01458 rmlo 1568 61 92 40 4 0 0.0002163475874112919
DBT-P05049 DBT-S01458 rmlo 1205 142 1138 126 4 0 0.0001676762185525149
DBT-P05049 DBT-S01458 rmlo 1248 78 1158 89 4 0 0.0001269022177439183
DBT-P05049 DBT-S01458 rmlo 1612 44 111 40 4 0 0.00011179190187249333
DBT-P05049 DBT-S01458 rmlo 1596 61 412 63 7 0 0.000166788071510382
DBT-P05049 DBT-S01458 rmlo 1606 42 416 39 7 0 0.00011207315401406959
DBT-P05049 DBT-S01458 rmlo 1120 72 1838 78 18 0 0.00011269836249994114
DBT-P05049 DBT-S01458 rmlo 1094 107 1788 134 18 0 0.00011066371371271089
DBT-P05049 DBT-S01458 rmlo 1551 56 1386 48 18 0 0.00010488247062312439
DBT-P05049 DBT-S01458 rmlo 1692 78 900 79 19 0 0.00024920733994804323
DBT-P05049 DBT-S01458 rmlo 1258 38